In [ ]:
import pandas as pd
import numpy as np
import math
import pickle

from scipy import stats
import scipy.io
from scipy.spatial.distance import pdist
from scipy.linalg import cholesky
from scipy.io import loadmat

import matlab.engine as engi
import matlab as mat

from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import SVC
from sklearn.metrics import classification_report,roc_auc_score,recall_score,precision_score
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.ensemble import RandomForestClassifier
from sklearn.decomposition import PCA
from pyearth import Earth

from src import SMOTE
from src import CFS
from src import metrices_V2 as metrices

import platform
from os import listdir
from os.path import isfile, join
from glob import glob
from pathlib import Path
import sys
import os
import copy
import traceback
from pathlib import Path

import matplotlib.pyplot as plt

In [48]:
def load_data(project):
    understand_path = 'data/understand_files_all/' + project + '_understand.csv'
    commit_guru_file_level_path = 'data/commit_guru_file_level/' + project + '_file.csv'
    commit_guru_path = 'data/commit_guru/' + project + '.csv'
    commit_guru_file_level_df = pd.read_csv(commit_guru_file_level_path)
    commit_guru_file_level_df['commit_hash'] = commit_guru_file_level_df.commit_hash.str.strip('"')
    commit_guru_df = pd.read_csv(commit_guru_path)
    commit_guru_df = commit_guru_df[['commit_hash','entrophy','nf']]
    values = {'contains_bug': False}
    commit_guru_df = commit_guru_df.fillna(values)
    process_df = commit_guru_file_level_df.merge(commit_guru_df,on='commit_hash')
    process_df = process_df[process_df['file_name'].str.contains('.java')]
    process_df = process_df.reset_index(drop = True)
    process_df['Name'] = process_df.file_name.str.rsplit('java/',1).str[1].str.split('.').str[0].str.replace('/','.')
    process_df = process_df.drop('file_name',axis = 1)

    understand_df = pd.read_csv(understand_path)
    understand_df = understand_df.dropna(axis = 1,how='all')
    cols_list = understand_df.columns.values.tolist()
    for item in ['Kind', 'Name','commit_hash', 'Bugs']:
        if item in cols_list:
            cols_list.remove(item)
            cols_list.insert(0,item)
    understand_df = understand_df[cols_list]
    commit_guru_df = pd.read_csv(commit_guru_path)
    cols = understand_df.columns.tolist()
    understand_df['Name'] = understand_df.Name#.str.rsplit('.',1).str[1]

    understand_df = understand_df.drop_duplicates(cols[4:len(cols)])
    df = understand_df.merge(process_df,on=['commit_hash','Name'])
#     df = df.drop(['AvgCyclomatic',
#        'AvgCyclomaticModified', 'AvgCyclomaticStrict', 'AvgEssential',
#        'AvgLine', 'AvgLineBlank', 'AvgLineCode', 'AvgLineComment',
#        'CountClassBase', 'CountClassCoupled', 'CountClassCoupledModified',
#        'CountClassDerived', 'CountDeclClassMethod', 'CountDeclClassVariable',
#        'CountDeclInstanceMethod', 'CountDeclInstanceVariable',
#        'CountDeclMethod', 'CountDeclMethodAll', 'CountDeclMethodDefault',
#        'CountDeclMethodPrivate', 'CountDeclMethodProtected',
#        'CountDeclMethodPublic', 'CountLine', 'CountLineBlank',
#        'CountLineCodeDecl', 'CountLineCodeExe', 'CountLineComment',
#        'CountSemicolon', 'CountStmt', 'CountStmtDecl', 'CountStmtExe',
#        'MaxCyclomatic', 'MaxCyclomaticModified', 'MaxCyclomaticStrict',
#        'MaxEssential', 'MaxInheritanceTree', 'MaxNesting',
#        'PercentLackOfCohesion', 'PercentLackOfCohesionModified',
#        'RatioCommentToCode', 'SumCyclomatic', 'SumCyclomaticModified',
#        'SumCyclomaticStrict', 'SumEssential'],axis = 1)
    cols = df.columns.tolist()
    cols.remove('Bugs')
    cols.append('Bugs')
    df = df[cols]
    for item in ['Kind', 'Name','commit_hash']:
        if item in cols:
            df = df.drop(labels = [item],axis=1)
    df.dropna(inplace=True)
    df.reset_index(drop=True, inplace=True)
#     df.to_csv('data/converted/'+ project + '_understand.csv',index=False)
    y = df.Bugs
    X = df.drop('Bugs',axis = 1)
    cols = X.columns
    scaler = MinMaxScaler()
    X = scaler.fit_transform(X)
    X = pd.DataFrame(X,columns = cols)
    return X,y

def apply_smote(df):
    cols = df.columns
    smt = SMOTE.smote(df)
    df = smt.run()
    df.columns = cols
    return df

def apply_cfs(df):
        y = df.Bugs.values
        X = df.drop(labels = ['Bugs'],axis = 1)
        X = X.values
        selected_cols = CFS.cfs(X,y)
        cols = df.columns[[selected_cols]].tolist()
        cols.append('Bugs')
        return df[cols],cols

In [50]:
def load_data(project):
    understand_path = 'data/understand_files_all/' + project + '_understand.csv'
    commit_guru_file_level_path = 'data/commit_guru_file_level/' + project + '_file.csv'
    commit_guru_path = 'data/commit_guru/' + project + '.csv'
    commit_guru_file_level_df = pd.read_csv(commit_guru_file_level_path)
    commit_guru_file_level_df['commit_hash'] = commit_guru_file_level_df.commit_hash.str.strip('"')
    commit_guru_df = pd.read_csv(commit_guru_path)
    commit_guru_df_parent = commit_guru_df[['parent_hashes','commit_hash','entrophy','nf']]
    commit_guru_df = commit_guru_df[['commit_hash','entrophy','nf']]
    values = {'contains_bug': False}
    commit_guru_df = commit_guru_df.fillna(values)
    
    commit_guru_df_parent['parent_hashes'] = commit_guru_df_parent.parent_hashes.str.split(' ').str[0]
    commit_guru_df_parent_file = commit_guru_file_level_df.merge(commit_guru_df_parent,on='commit_hash')
    commit_guru_df_parent_file = commit_guru_df_parent_file.drop('commit_hash',axis = 1)
    commit_guru_df_parent_file.rename(columns={'parent_hashes':'commit_hash'},inplace=True)
    commit_guru_df_parent_file = commit_guru_df_parent_file[commit_guru_df_parent_file['file_name'].str.contains('.java')]
    commit_guru_df_parent_file = commit_guru_df_parent_file.reset_index(drop = True)
    commit_guru_df_parent_file['Name'] = commit_guru_df_parent_file.file_name.str.rsplit('java/',1).str[1].str.split('.').str[0].str.replace('/','.')
    commit_guru_df_parent_file = commit_guru_df_parent_file.drop('file_name',axis = 1)
    
    
    commit_guru_df_file = commit_guru_file_level_df.merge(commit_guru_df,on='commit_hash')
    commit_guru_df_file = commit_guru_df_file[commit_guru_df_file['file_name'].str.contains('.java')]
    commit_guru_df_file = commit_guru_df_file.reset_index(drop = True)
    commit_guru_df_file['Name'] = commit_guru_df_file.file_name.str.rsplit('java/',1).str[1].str.split('.').str[0].str.replace('/','.')
    commit_guru_df_file = commit_guru_df_file.drop('file_name',axis = 1)
    
    process_df = pd.concat([commit_guru_df_file,commit_guru_df_parent_file],axis = 0)
    print(process_df.columns)

    understand_df = pd.read_csv(understand_path)
    understand_df = understand_df.dropna(axis = 1,how='all')
    cols_list = understand_df.columns.values.tolist()
    for item in ['Kind', 'Name','commit_hash', 'Bugs']:
        if item in cols_list:
            cols_list.remove(item)
            cols_list.insert(0,item)
    understand_df = understand_df[cols_list]
    commit_guru_df = pd.read_csv(commit_guru_path)
    cols = understand_df.columns.tolist()
    understand_df['Name'] = understand_df.Name#.str.rsplit('.',1).str[1]

    understand_df = understand_df.drop_duplicates(cols[4:len(cols)])
    df = understand_df.merge(process_df,on=['commit_hash','Name'])
    cols = df.columns.tolist()
    cols.remove('Bugs')
    cols.append('Bugs')
    df = df[cols]
    for item in ['Kind', 'Name','commit_hash']:
        if item in cols:
            df = df.drop(labels = [item],axis=1)
    df.dropna(inplace=True)
    cols = df.columns.tolist()
    df = df.drop_duplicates(cols[:-1])
    df.reset_index(drop=True, inplace=True)

#     df.to_csv('data/converted/'+ project + '_understand.csv',index=False)
    y = df.Bugs
    X = df.drop('Bugs',axis = 1)
    cols = X.columns
    scaler = MinMaxScaler()
    X = scaler.fit_transform(X)
    X = pd.DataFrame(X,columns = cols)
    return X,y


In [44]:
def run_self(project):
    X,y = load_data(project)
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.40, random_state=18)
    loc = X_test.CountLineCode
    print(X_test.shape)
    X_train = X_train.drop('CountLineCode',axis = 1)
    X_test = X_test.drop('CountLineCode',axis = 1)
    df_smote = pd.concat([X_train,y_train],axis = 1)
    df_smote = apply_smote(df_smote)
    y_train = df_smote.Bugs
    X_train = df_smote.drop('Bugs',axis = 1)
    clf =  SVC()
    clf.fit(X_train,y_train)
#     importance = clf.feature_importances_
    importance = 0
    predicted = clf.predict(X_test)
    abcd = metrices.measures(y_test,predicted,loc)
    pf = abcd.get_pf()
    recall = abcd.calculate_recall()
    precision = abcd.calculate_precision()
    f1 = abcd.calculate_f1_score()
    g_score = abcd.get_g_score()
    pci_20 = abcd.get_pci_20()
    ifa = abcd.get_ifa()
    try:
        auc = roc_auc_score(y_test, predicted)
    except:
        auc = 0
    print(classification_report(y_test, predicted))
    return recall,precision,pf,f1,g_score,auc,pci_20,ifa,importance

In [43]:
def run_self_CFS(project):
    X,y = load_data(project)
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.40, random_state=18)
    loc = X_test.CountLineCode
    df_smote = pd.concat([X_train,y_train],axis = 1)
    df_smote = apply_smote(df_smote)
    df_smote,cols = apply_cfs(df_smote)
    y_train = df_smote.Bugs
    X_train = df_smote.drop('Bugs',axis = 1)
    clf = SVC()
    clf.fit(X_train,y_train)
    importance = 0
    predicted = clf.predict(X_test[cols[:-1]])
    abcd = metrices.measures(y_test,predicted,loc)
    pf = abcd.get_pf()
    recall = abcd.calculate_recall()
    precision = abcd.calculate_precision()
    f1 = abcd.calculate_f1_score()
    g_score = abcd.get_g_score()
    pci_20 = abcd.get_pci_20()
    ifa = abcd.get_ifa()
    try:
        auc = roc_auc_score(y_test, predicted)
    except:
        auc = 0
    print(classification_report(y_test, predicted))
    return recall,precision,pf,f1,g_score,auc,pci_20,ifa,importance

In [46]:
proj_df = pd.read_csv('projects.csv')
projects = proj_df.repo_name.tolist()

In [52]:
precision_list = {}
recall_list = {}
pf_list = {}
f1_list = {}
g_list = {}
auc_list = {}
pci_20_list = {}
ifa_list = {}
featue_importance = {}
for project in projects:
    try:
        if project == '.DS_Store':
            continue
#         if project != 'org.alloytools.alloy':
#             continue
#         if project != 'exhibitor':
#             continue
        print("+++++++++++++++++   "  + project + "  +++++++++++++++++")
        recall,precision,pf,f1,g_score,auc,pci_20,ifa,importance = run_self(project)
        recall_list[project] = recall
        precision_list[project] = precision
        pf_list[project] = pf
        f1_list[project] = f1
        g_list[project] = g_score
        auc_list[project] = auc
        pci_20_list[project] = pci_20
        ifa_list[project] = ifa
        featue_importance[project] = importance
    except Exception as e:
        print(e)
        continue
final_result = {}
final_result['precision'] = precision_list
final_result['recall'] = recall_list
final_result['pf'] = pf_list
final_result['f1'] = f1_list
final_result['g'] = g_list
final_result['auc'] = auc_list
final_result['pci_20'] = pci_20_list
final_result['ifa'] = ifa_list
final_result['featue_importance'] = featue_importance
# with open('results/Performance/With_median_commit_guru_data/with_diff_models/process+product_1000_nb.pkl', 'wb') as handle:
#     pickle.dump(final_result, handle, protocol=pickle.HIGHEST_PROTOCOL)

+++++++++++++++++   org.alloytools.alloy  +++++++++++++++++
Index(['Name', 'age', 'commit_hash', 'entrophy', 'exp', 'la', 'ld', 'lt', 'nd',
       'ndev', 'nf', 'ns', 'nuc', 'rexp', 'sexp'],
      dtype='object')
Found array with 0 sample(s) (shape=(0, 58)) while a minimum of 1 is required by MinMaxScaler.
+++++++++++++++++   qpython  +++++++++++++++++
Index(['Name', 'age', 'commit_hash', 'entrophy', 'exp', 'la', 'ld', 'lt', 'nd',
       'ndev', 'nf', 'ns', 'nuc', 'rexp', 'sexp'],
      dtype='object')
Found array with 0 sample(s) (shape=(0, 58)) while a minimum of 1 is required by MinMaxScaler.
+++++++++++++++++   friendlychat-android  +++++++++++++++++
Index(['Name', 'age', 'commit_hash', 'entrophy', 'exp', 'la', 'ld', 'lt', 'nd',
       'ndev', 'nf', 'ns', 'nuc', 'rexp', 'sexp'],
      dtype='object')
(10, 58)
The number of classes has to be greater than one; got 1 class
+++++++++++++++++   paho.mqtt.android  +++++++++++++++++
Index(['Name', 'age', 'commit_hash', 'entrophy', 'exp', 

KeyboardInterrupt: 

In [ ]:
np.median(list(recall_list.values()))

In [ ]:
df1,df2,df3=load_data('exhibitor')

In [67]:
project = 'org.alloytools.alloy'
df = pd.read_csv('data/commit_guru_file_level/' + project + '_file.csv')

In [68]:
df

commit_hash  \
0     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
19    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
20    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
21    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
22    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
23    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
24    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
25    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
26    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
27    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
28    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
29    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
...                                         ...   
7562  362670a78adbf93920cfe3d301e8f21c3b66faae"   
7563  362670a78adbf93920cfe3d301e8f21c3b66faae"   
7564  362670a78adbf93920cfe3d301e8f21c3b66faae"   
7565  362670a78adbf93920cfe3d301e8f21c3b66faae"   
7566  c922882cdfab98babe16119cc4f10ef827213eac"   
7567  c922882cdfab98babe16119cc4f10ef827213eac"   
7568  c922882cdfab98babe16119cc4f10ef827213eac"   
7569  c922882cdfab98babe16119cc4f10ef827213eac"   
7570  c922882cdfab98babe16119cc4f10ef827213eac"   
7571  2d5b4e0ff0a6daffceb58d8b761aed8a3df74894"   
7572  c13d9230cca10d5fa75d0f165cfb32c3126916eb"   
7573  6cc807ac0a7d9899304e2af38c4c234f12680ed8"   
7574  4f6f34c261c9a27d7a46ba7bf3cfe9df0802addf"   
7575  4f6f34c261c9a27d7a46ba7bf3cfe9df0802addf"   
7576  4f6f34c261c9a27d7a46ba7bf3cfe9df0802addf"   
7577  4f6f34c261c9a27d7a46ba7bf3cfe9df0802addf"   
7578  4f6f34c261c9a27d7a46ba7bf3cfe9df0802addf"   
7579  4f6f34c261c9a27d7a46ba7bf3cfe9df0802addf"   
7580  4f6f34c261c9a27d7a46ba7bf3cfe9df0802addf"   
7581  4f6f34c261c9a27d7a46ba7bf3cfe9df0802addf"   
7582  a3a36d82f960aeed2fb4ce2ead3933e121ce92a1"   
7583  9f95aa0f7b045861da0890340b5d5cc01032b07d"   
7584  cf6f59d8119babd9b3278ff116c3c60e5dd7bc8c"   
7585  cf6f59d8119babd9b3278ff116c3c60e5dd7bc8c"   
7586  cf6f59d8119babd9b3278ff116c3c60e5dd7bc8c"   
7587  cf6f59d8119babd9b3278ff116c3c60e5dd7bc8c"   
7588  cf6f59d8119babd9b3278ff116c3c60e5dd7bc8c"   
7589  cf6f59d8119babd9b3278ff116c3c60e5dd7bc8c"   
7590  cf6f59d8119babd9b3278ff116c3c60e5dd7bc8c"   
7591  b3c51ff79d55d22fd5893e607847d925eb031859"   

                                              file_name   la   ld    lt  \
0                                            .gitignore    3    0     0   
1                                               LICENSE   21    0     0   
2                                             README.md  119    0     0   
3                                     deploy/.gitignore    4    0     0   
4                                      deploy/README.md   24    0     0   
5                                  deploy/bin/deploy.sh   24    0     0   
6     deploy/litemall-admin-api/litemall-admin-api.conf    2    0     0   
7           deploy/litemall-os-api/litemall-os-api.conf    2    0     0   
8           deploy/litemall-wx-api/litemall-wx-api.conf    2    0     0   
9                                              doc/1.md  446    0     0   
10                                             d

In [69]:
df = df[df['file_name'].str.contains('.java')]
df = df.reset_index(drop=True)

In [70]:
u_commits = df.commit_hash.unique()
u_files = df.file_name.unique()

In [71]:
final_df = pd.DataFrame()
for commit in u_commits:
    commit_df = df[df['commit_hash'] == commit]
    cols = commit_df.columns
    start_index = commit_df.index[0]
    sub_df = df.loc[:start_index-1]
    metrics = []
    for file in u_files:
        if file not in list(commit_df.file_name.unique()):
            sub_df_file = sub_df[sub_df['file_name'] == file]
            sub_df_file = sub_df_file.reset_index(drop = True)
            if sub_df_file.shape[0] > 0:
#                 print(sub_df_file)
                metrics.append(sub_df_file.loc[sub_df_file.shape[0]-1].values.tolist()[1:])
    metrics_df = pd.DataFrame(metrics,columns = cols[1:])
    metrics_df['commit_hash'] = [commit]*metrics_df.shape[0]
    metrics_df = metrics_df[['commit_hash','file_name', 'la', 'ld', 'lt', 'age', 
                          'ndev', 'nuc', 'ns', 'exp', 'sexp', 'rexp', 'nd']]
    metrics_df = pd.concat([metrics_df,commit_df],axis = 0)
    final_df = pd.concat([final_df,metrics_df],axis = 0)
    print(final_df)

                                   commit_hash  \
0    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18   6c14c43cba6c9ecdd842271736b96e60054be8d0"   


                                   commit_hash  \
0    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18   6c14c43cba6c9ecdd842271736b96e60054be8d0"   


                                   commit_hash  \
0    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18   6c14c43cba6c9ecdd842271736b96e60054be8d0"   


                                   commit_hash  \
0    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18   6c14c43cba6c9ecdd842271736b96e60054be8d0"   


                                   commit_hash  \
0    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17   6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18   6c14c43cba6c9ecdd842271736b96e60054be8d0"   


...

                                    commit_hash  \
0     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18    6c14c43cba6c9ecdd84227173

                                    commit_hash  \
0     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18    6c14c43cba6c9ecdd84227173

                                    commit_hash  \
0     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18    6c14c43cba6c9ecdd84227173

                                    commit_hash  \
0     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18    6c14c43cba6c9ecdd84227173

                                    commit_hash  \
0     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
1     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
2     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
3     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
4     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
5     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
6     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
7     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
8     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
9     6c14c43cba6c9ecdd842271736b96e60054be8d0"   
10    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
11    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
12    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
13    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
14    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
15    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
16    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
17    6c14c43cba6c9ecdd842271736b96e60054be8d0"   
18    6c14c43cba6c9ecdd84227173

In [58]:
final_df.shape

(169141, 13)

In [59]:
# final_df['Name'] = final_df.file_name.str.rsplit('java/',1).str[1].str.split('.').str[0].str.replace('/','.')
final_df['commit_hash'] = final_df.commit_hash.str.strip('"')


In [60]:
final_df.drop('file_name',inplace = True,axis = 1)

In [61]:
understand_df = pd.read_csv('data/understand_files_all/' + project + '_understand.csv')

In [62]:
understand_df = understand_df.dropna(axis = 1,how='all')
cols_list = understand_df.columns.values.tolist()
for item in ['Kind', 'Name','commit_hash', 'Bugs']:
    if item in cols_list:
        cols_list.remove(item)
        cols_list.insert(0,item)
understand_df = understand_df[cols_list]
cols = understand_df.columns.tolist()
understand_df['Name'] = understand_df.Name
understand_df = understand_df.drop_duplicates(cols[4:len(cols)])

In [63]:
df_merged = understand_df.merge(final_df,on=['commit_hash','Name'])

KeyError: 'Name'

In [40]:
y = df_merged.Bugs
X = df_merged.drop(['Bugs','commit_hash','Name','Kind'],axis = 1)

In [41]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.40, random_state=18)

In [42]:
X_test.shape

(278, 56)

In [66]:
len(u_commits)

429